## Create _df_preloaded
This notebook is for archival purposes to document how the 'create_df_preloaded' was created.

In [4]:
import predread_io as io
import textproc_lex as lex

# this is the next one to adjust
# from charproc.character_stats import (get_static_charstats, get_uniquness_points)

import pandas as pd
import numpy as np

import sys
from pathlib import Path
path = sys.path[0]
charpath= path + '/materials'

from config import DEFAULT_LAMBS,PIXPERCHAR,TEXT_NRS,PROJ_ROOT
from copy import deepcopy

import seaborn as sns
import matplotlib.pyplot as plt

import time
import resources

In [5]:
from pdb import set_trace

In [6]:
### Below we load the thingie 

In [8]:
corpname='provo'
save_again=False
for corpname in ('dundee','geco','provo'):
    
    
    print("--"*40)
    print("now doing corpus: ",corpname)
    # corpus specific settings 
    US=True if corpname=='provo' else False
    text_nrs=TEXT_NRS[corpname]

    # load corpus, and mark bad 
    tstart=time.time()
    corpus=getattr(io,f'{corpname}_load_df')() 
    print(f'loading took: {round(time.time()-tstart,2)} secs')
    
    # then we get the gpt anlysed dictionary (anlysed used pipe_process_lex.py)
    analyseddict = io.load_full_gpt_pickled(corpname) # and the unigram info
    analyseddict = lex.dict_add_unigram(text_nrs, analyseddict,corpus, corpname,US=US)

    # we add it to the dataframe 
    tstart=time.time()
    corpus = getattr(lex,f'{corpname}_add_GPT2')(corpus, text_nrs, analyseddict=analyseddict, 
                                                 additional=True,unigram=True)
    print(f'adding gpt took: {round(time.time()-tstart,2)} secs')

    # now we add the parafoveal stats 
    corpus = io.add_parafov(corpus,corpname,lambda_pars=DEFAULT_LAMBS)
    corpus = io.add_parafov(corpus,corpname,lambda_pars=DEFAULT_LAMBS,contextual=True)
    print('just added parafov')
    # finally we mark bads as bad, and clean up the inf values 
    corpus = getattr(io,f'{corpname}_mark_bad')(corpus)
    corpus = io.cleanup_infs(corpus,PIXPERCHAR[corpname])

    out_name=PROJ_ROOT / 'materials' / corpname.upper()  / f'{corpname}_df_preloaded.csv'
    if save_again:
        corpus.to_csv(out_name)

--------------------------------------------------------------------------------
now doing corpus:  dundee
Loading csv from: /project/3018039.02/predread/resources/Dundee/TextMaterial.csv ...
Loading csv from: /project/3018039.02/predread/resources/Dundee/Word_Data.csv ...
Loading csv from: /project/3018039.02/predread/resources/Dundee/Dundee_DLT_freq_goldtok_nonan_newFPD.csv ...
Loading csv from: /project/3018039.02/predread/resources/Dundee/Fixation_Data.csv ...
Dundee loaded, dataframe size: (515010, 62).
loading took: 30.41 secs
adding gpt took: 390.06 secs
just added parafov
--------------------------------------------------------------------------------
now doing corpus:  geco
Loading csv from: /project/3018039.02/predread/resources/GECO/EnglishMaterial_SENTENCE.csv ...
Loading csv from: /project/3018039.02/predread/resources/GECO/MonolingualReadingData_DATA.csv ...
Loading csv from: /project/3018039.02/predread/resources/GECO/EnglishMaterial_ALL.csv ...
GECO loaded, dataframe si

In [9]:
src='/project/3018039.02/predread/materials/DUNDEE_GPT2_ALL_TEXTS.p'
trg='/project/3018039.02/predread_sc/materials/DUNDEE_GPT2_ALL_TEXTS.p'
# shutil.cop
# import shutil
shutil.copy2(src,trg)

'/project/3018039.02/predread_sc/materials/DUNDEE_GPT2_ALL_TEXTS.p'

In [15]:
import imp
imp.reload(io)

<module 'predread_io' from '/project/3018039.02/predread/predread_io.py'>

In [16]:
geco_prel_new=io.load_df_preloaded('geco')
geco_prel_old=io.geco_load_df_preloaded()

In [25]:
def unnest_list(l):
    """convert nested list to list (in case I forgot about list comprehesions"""
    return([item for sublist in l for item in sublist])


In [20]:
geco_prel_new_4=geco_prel_new[geco_prel_new['Text_Nr']==4]
geco_prel_old_4=geco_prel_old[geco_prel_old['Text_Nr']==4]